![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo I 2013 Cobertura de Plano de Saúde

## Bibliotecas Utilizadas

In [3]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [4]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2013>")

[1] 222385   1000

## Definição do peso e filtragem de respondentes do questionário

In [5]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2013.1<- <Coloque aqui o nome do arquivo RDATA> %>% mutate(peso_moradores=((V00281*205546/199551444)))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_moradores))
summary(pns2013.1$peso_moradores)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.009731  0.282509  0.547672  1.000000  1.205104 13.898464 

## Criação de variáveis dos indicadores

In [6]:
#Desfechos - Indicadores

#Posse de plano de saúde médico ou odontológico particular - I001P
pns2013.1 <- pns2013.1 %>% mutate(I001P= ifelse(I001==1, 1,2))
pns2013.1$I001P<-factor(pns2013.1$I001P, levels=c(1,2), labels=c("Sim", "Não"))
summary(pns2013.1$I001P) 



##Posse de plano de saúde médico particular  - I002P
pns2013.1 <- pns2013.1 %>% mutate(I002P = ifelse(I001==2 ,2,
                                          ifelse(I001==1 & I002==1 & I003==1,2,        
                                          ifelse(I001==1 & I002==1 & I003==2,1,
                                          ifelse(I001==1 & I002>1  & I003==1,1,
                                          ifelse(I001==1 & I002>1  & I003==2,1,2))))))                                   
pns2013.1$I002P<-factor(pns2013.1$I002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$I002P)


#Posse de plano de saúde odontológico particular  - I003P - Plano amostral distinto
pns2013.1 <- pns2013.1 %>% mutate(I003P= if_else(I003==1,1,2))
pns2013.1$I003P<-factor(pns2013.1$I003P, levels=c(1,2), labels=c("Sim", "Não"))
summary(pns2013.1$I003P)


Sim    Não 
 50692 154854

Sim    Não 
 43957 161589

Sim    Não   NA's 
 10040  40652 154854

## Definições de abrangências

### Situação urbana ou rural

In [7]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Situação_Urbano_Rural=V0026)
pns2013.1$Situação_Urbano_Rural<-factor(pns2013.1$Situação_Urbano_Rural, levels=c(1,2), labels=c("Urbano", "Rural"))
summary(pns2013.1$Situação_Urbano_Rural)

Urbano  Rural 
166580  38966

### Sexo

In [8]:
#Sexo
pns2013.1 <- pns2013.1 %>% rename(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

Masculino  Feminino 
    99236    106310

### UF

In [9]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federação=V0001)
pns2013.1$Unidades_da_Federação<-factor(pns2013.1$Unidades_da_Federação, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federação)

Rondônia                Acre            Amazonas             Roraima 
               5883                6754               11194                6409 
               Pará               Amapá           Tocantins            Maranhão 
               9079                6072                5125                6650 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               6326                9179                6004                6197 
         Pernambuco             Alagoas             Sergipe               Bahia 
               8705                6376                5588                8391 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
              11800                5502               10445               17072 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               9389                4969                8255                5760 
        Mato Grosso               Goiás    Distrito Federal 
               4803                7710                5909

### Grandes Regiões

In [10]:
#Grandes Regiões
pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federação, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       50516        63416        44819        22613        24182

### Capital

In [11]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federação,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2013.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          5883           6754          11194           6409           9079 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          6072           5125           6650           6326           9179 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          6004           6197           8705           6376           5588 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          8391          11800           5502          10445          17072 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          9389           4969           8255           5760           4803 
       Goiânia       Brasília 
          7710           5909

### Faixa Etária

In [12]:
#Faixas Etárias
pns2013.1 <- pns2013.1 %>% mutate(faixa_idade = ifelse(C008<=0,1, 
                        ifelse(C008%in% 1:4, 2, 
                        ifelse(C008%in% 5:14, 3,
                        ifelse(C008%in% 15:24, 4,
                        ifelse(C008%in% 25:34, 5,
                        ifelse(C008%in% 35:44, 6,
                        ifelse(C008%in% 45:59, 7,8))))))))

pns2013.1$faixa_idade<-factor(pns2013.1$faixa_idade, levels=c(1,2,3,4,5,6,7,8), labels=c("Menor de 1 ano","1 a 4 anos","5 a 14 anos","15 a 24 anos","25 a 34 anos","35 a 44 anos","45 a 59 anos","60 anos ou mais"))
summary(pns2013.1$faixa_idade) 

Menor de 1 ano      1 a 4 anos     5 a 14 anos    15 a 24 anos    25 a 34 anos 
           2736           11713           33951           36020           33406 
   35 a 44 anos    45 a 59 anos 60 anos ou mais 
          29562           34343           23815

### Raça

In [13]:
#Raça
pns2013.1 <- pns2013.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))

pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2013.1$Raca)

Branca  Preta  Parda   NA's 
 78177  17461 106910   2998

### Renda per capita

In [14]:
#Rendimento domiciliar per capita - Outro plano amostral

pns2013.1 <- pns2013.1 %>% mutate(VDF004= ifelse(VDF003 %in% 0:170, 1, 
                        ifelse(VDF003%in% 170:339, 2, 
                        ifelse(VDF003%in% 340:678, 3,
                        ifelse(VDF003%in% 679:1356, 4,
                        ifelse(VDF003%in% 1357:2034, 5,
                        ifelse(VDF003%in% 2035:3390, 6,
                        ifelse(VDF003=="NA","NA",7))))))))


pns2013.1 <- pns2013.1 %>% mutate(rend_per_capita= ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004==3, 2, 
                        ifelse(VDF004==4, 3,
                        ifelse(VDF004==5, 4,
                        ifelse(VDF004=="NA","NA",5))))))
                                                  
pns2013.1$rend_per_capita<-factor(pns2013.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2013.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       61683        61662        47265        14910        19802          224

## Criando indicadores

### Filtrando base de indicadores

In [15]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2013survey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_moradores", "I001P","I002P","I003P", "V0031","C009","VDF003",
                                     "Situação_Urbano_Rural","Sexo","Unidades_da_Federação", "GrandesRegioes",
                                     "Capital","faixa_idade", "Raca","rend_per_capita")
summary(pns2013survey)

     V0024            UPA_PNS        peso_moradores      I001P       
 Min.   :1110011   Min.   :1100001   Min.   : 0.009731   Sim: 50692  
 1st Qu.:2110011   1st Qu.:2100025   1st Qu.: 0.282509   Não:154854  
 Median :2851010   Median :2800091   Median : 0.547672               
 Mean   :2931340   Mean   :2903832   Mean   : 1.000000               
 3rd Qu.:3532013   3rd Qu.:3500397   3rd Qu.: 1.205104               
 Max.   :5310220   Max.   :5300180   Max.   :13.898464               
                                                                     
 I002P         I003P            V0031            C009           VDF003        
 Sim: 43957   Sim : 10040   Min.   :1.000   Min.   :1.000   Min.   :     0.0  
 Não:161589   Não : 40652   1st Qu.:1.000   1st Qu.:1.000   1st Qu.:   300.0  
              NA's:154854   Median :2.000   Median :4.000   Median :   553.0  
                            Mean   :2.309   Mean   :2.689   Mean   :   973.9  
                            3rd Qu.:4.000   3

### Exporta tabela filtrada com os dados específicos - Módulo I 2013

In [17]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2013survey, file.path(diretorio_saida, "pns2013Isurvey.csv"))

### Cria plano amostral complexo

In [18]:
#survey design
desPNSI=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_moradores, nest=TRUE, data=pns2013survey)
desPNSIC=subset(desPNSI, V0031==1)
desPNSIR=subset(desPNSI, C009!=9)
desPNSIRE=subset(desPNSI, VDF003!=9)

In [19]:
#survey design - I003P
desPNSI003P=subset(desPNSI, !is.na(I003P))
desPNSI003P_R=subset(desPNSI, !is.na(I003P) & C009!=9)
desPNSI003P_C=subset(desPNSI, V0031==1 & !is.na(I003P))
desPNSI003P_RE=subset(desPNSI, VDF003!=9 & !is.na(I003P))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [20]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [21]:
ListaIndicadores = c(~I001P,~I002P,~I003P)
ListaIndicadoresTexto = c("I001P","I002P","I003P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Situação_Urbano_Rural,~Unidades_da_Federação,~GrandesRegioes,~Capital)
ListaDominiosTexto = c("Sexo","raça","rend_per_capita","fx_idade","urb_rur","uf","região","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

#### Preenchendo a tabela de indicadores

In [22]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    for (dominio in ListaDominios){
               if (ListaDominiosTexto[j]=="capital"){
                   if(ListaIndicadoresTexto[i] == "I003P"){
                           dataframe_indicador<-svyby( indicador , dominio , desPNSI003P_C , svymean,vartype= c("ci","cv"))
                }else{
                       dataframe_indicador<-svyby( indicador , dominio , desPNSIC , svymean,vartype= c("ci","cv"))
                }
                   
               }else if (ListaDominiosTexto[j]=="raça"){
                   if(ListaIndicadoresTexto[i] == "I003P"){
                           dataframe_indicador<-svyby( indicador , dominio , desPNSI003P_R , svymean,vartype= c("ci","cv"))
                    }else{
                       dataframe_indicador<-svyby( indicador , dominio , desPNSIR , svymean,vartype= c("ci","cv"))
                   }
                }else if (ListaDominiosTexto[j]=="rend_per_capita"){
                   if(ListaIndicadoresTexto[i] == "I003P"){
                           dataframe_indicador<-svyby( indicador , dominio , desPNSI003P_RE , svymean,vartype= c("ci","cv"))
                    }else{
                       dataframe_indicador<-svyby( indicador , dominio , desPNSIRE , svymean,vartype= c("ci","cv"))
                   }
               }else {
                   if(ListaIndicadoresTexto[i] == "I003P"){
                           dataframe_indicador<-svyby( indicador , dominio , desPNSI003P , svymean,vartype= c("ci","cv"))
                   }else{
                       dataframe_indicador<-svyby( indicador , dominio , desPNSI , svymean,vartype= c("ci","cv"))
                   }
               }
               
                dataframe_indicador<-data.frame(dataframe_indicador)
              
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }
}




#### Criando a tabela pela abrangência total

In [23]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [24]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
         if (total == "Capital"){
                   if(ListaIndicadoresTexto[i] == "I003P"){
                           dataframe_indicador <- svymean(indicador,desPNSI003P_C)
                   }else{
                       dataframe_indicador <- svymean(indicador,desPNSIC)
                   }
                   
        } else {
                   if(ListaIndicadoresTexto[i] == "I003P"){
                           dataframe_indicador <- svymean(indicador,desPNSI003P)
                    }else{
                       dataframe_indicador <- svymean(indicador,desPNSI)
                   }
        }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                               select('Sim','LowerS','UpperS','cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
        
    }
}


#### Unindo tabela de indicadores e de totais

In [25]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando a tabela de indicadores

In [26]:
matrizIndicadores

abr_tipo        abr_nome        Ano  Indicador Sim       
Masculino       Sexo            Masculino       2013 I001P     0.26983320
Feminino        Sexo            Feminino        2013 I001P     0.28801583
Branca          raça            Branca          2013 I001P     0.37882551
Preta           raça            Preta           2013 I001P     0.21596686
Parda           raça            Parda           2013 I001P     0.18694179
Até 1/2 SM      rend_per_capita Até 1/2 SM      2013 I001P     0.06450625
1/2 até 1 SM    rend_per_capita 1/2 até 1 SM    2013 I001P     0.17103434
1 até 2 SM      rend_per_capita 1 até 2 SM      2013 I001P     0.34847575
2 até 3 SM      rend_per_capita 2 até 3 SM      2013 I001P     0.56498715
Mais de 3 SM    rend_per_capita Mais de 3 SM    2013 I001P     0.75143120
Menor de 1 ano  fx_idade        Menor de 1 ano  2013 I001P     0.29083867
1 a 4 anos      fx_idade        1 a 4 anos      2013 I001P     0.26735953
5 a 14 anos     fx_idade        5 a 14 anos     2013 I001P     0.21974653
15 a 24 anos    fx_idade        15 a 24 anos    2013 I001P     0.23512686
25 a 34 anos    fx_idade        25 a 34 anos    2013 I001P     0.29870350
35 a 44 anos    fx_idade        35 a 44 anos    2013 I001P     0.31207709
45 a 59 anos    fx_idade        45 a 59 anos    2013 I001P     0.30988835
60 anos ou mais fx_idade        60 anos ou mais 2013 I001P     0.30825680
Urbano          urb_rur         Urbano          2013 I001P     0.31692696
Rural           urb_rur         Rural           2013 I001P     0.06223760
Rondônia        uf              Rondônia        2013 I001P     0.13077603
Acre            uf              Acre            2013 I001P     0.07333861
Amazonas        uf              Amazonas        2013 I001P     0.15281298
Roraima         uf              Roraima         2013 I001P     0.08908189
Pará            uf              Pará            2013 I001P     0.13771743
Amapá           uf              Amapá           2013 I001P     0.12549356
Tocantins       uf              Tocantins       2013 I001P     0.11149619
Maranhão        uf              Maranhão        2013 I001P     0.06940109
Piauí           uf              Piauí           2013 I001P     0.11808861
Ceará           uf              Ceará           2013 I001P     0.15577904
⋮               ⋮               ⋮               ⋮    ⋮         ⋮         
Boa Vista2      capital         Boa Vista       2013 I003P     0.22380928
Belém2          capital         Belém           2013 I003P     0.20012415
Macapá2         capital         Macapá          2013 I003P     0.30410444
Palmas2         capital         Palmas          2013 I003P     0.15601426
São Luís2       capital         São Luís        2013 I003P     0.18489454
Teresina2       capital         Teresina        2013 I003P     0.10366346
Fortaleza2      capital         Fortaleza       2013 I003P     0.21196305
Natal2          capital         Natal           2013 I003P     0.27059747
João Pessoa2    capital         João Pessoa     2013 I003P     0.36652102
Recife2         capital         Recife          2013 I003P     0.17264920
Maceió2         capital         Maceió          2013 I003P     0.27472579
Aracaju2        capital         Aracaju         2013 I003P     0.21103284
Salvador2       capital         Salvador        2013 I003P     0.32501323
Belo Horizonte2 capital         Belo Horizonte  2013 I003P     0.15910470
Vitória2        capital         Vitória         2013 I003P     0.17856762
Rio de Janeiro5 capital         Rio de Janeiro  2013 I003P     0.23344613
São Paulo4      capital         São Paulo       2013 I003P     0.17286991
Curitiba2       capital         Curitiba        2013 I003P     0.23660232
Florianópolis2  capital         Florianópolis   2013 I003P     0.20172107
Porto Alegre2   capital         Porto Alegre    2013 I003P     0.08600525
Campo Grande2   capital         Campo Grande    2013 I003P     0.12346055
Cuiabá2         capital         Cuiabá          2013 I003P     0.18927629
Goiânia2        capi

#### Exportando tabela de indicadores calculados - Módulo I 2013

In [28]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida, Indicadores_2013I_R.csv",sep = ";",dec = ",",row.names = FALSE)